In [1]:
import numpy as np
import pandas as pd
import warnings
import matplotlib.pyplot as plt

In [2]:
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder
import scipy.sparse as sp
from scipy.sparse import hstack
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
import xgboost as xgb
from sklearn.ensemble import GradientBoostingClassifier, AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from tensorflow import keras
from keras.layers import Dense, Flatten, Input, Dropout, BatchNormalization, Activation
from keras import Sequential
import keras_tuner as kt

In [3]:
### Import Data
train = pd.read_csv('train.csv')
x_test = pd.read_csv('test.csv')
variables= train.columns

# get IDs of test observation. Necessary for csv file later
test_passenger_ids = x_test['PassengerId']

In [4]:
### Split Full Training Data in Training and Validation Data
#train, validation = train_test_split(train, test_size=0.2, random_state=42)
#train = pd.DataFrame(train, columns=variables)
#validation = pd.DataFrame(validation, columns=variables)

In [5]:
### Remove PassengerId, Name, Ticket (too many categories) and Cabin (too many NA values) Column
train.drop(['PassengerId', 'Cabin', 'Ticket'], axis=1, inplace=True)
#validation.drop(['PassengerId', 'Name', 'Cabin', 'Ticket'], axis=1, inplace=True)
x_test.drop(['PassengerId', 'Cabin', 'Ticket'], axis=1, inplace=True)

In [6]:
### Get Name Titles from Names

def get_titles(dat):
    
    titles = []
    for i, person in enumerate(dat['Name']):
        titles.append(person.split(', ')[1].split('. ')[0])
    dat['Titles'] = titles
    dat.drop('Name', axis=1, inplace=True)
    
    # Replace all other titles than Mr, Mrs, Miss and Master
    titles_index_nobles = (dat[dat['Titles'].str.contains('Don|Jonkheer|Lady|Sir')]).index 
    titles_index_officer = (dat[dat['Titles'].str.contains('Capt|Col|Major|Rev|Dr')]).index 
    titles_index_mrs = (dat[dat['Titles'].str.contains('Mlle|Ms|Mme')]).index 

    dat.loc[titles_index_nobles,'Titles'] = 'Noble'
    dat.loc[titles_index_officer,'Titles'] = 'Officer'
    dat.loc[titles_index_mrs,'Titles'] = 'Mrs'
    
    return dat    
    

train = get_titles(train)
x_test = get_titles(x_test)


In [7]:
### Combine SibSp and Parch into Number of family members
train['FamMebers'] = (train['SibSp'] + train['Parch']).astype(dtype='float64')
x_test['FamMebers'] = (x_test['SibSp'] + x_test['Parch']).astype(dtype='float64')

train.drop(['SibSp', 'Parch'], axis=1, inplace=True)
x_test.drop(['SibSp', 'Parch'], axis=1, inplace=True)



In [8]:
### Divide in X and Y data
def split_xy(dat, outcome):
    y = dat[outcome_variable]
    x = dat.drop(outcome_variable, axis=1)
    return x, y

outcome_variable = 'Survived'
x_train, y_train = split_xy(train, outcome_variable)
#x_val, y_val = split_xy(validation, outcome_variable)

In [9]:
### Impute Age Variable based on groups (because there are 177 NA values)
x_train['Age'] = x_train['Age'].fillna(x_train.groupby(['Pclass', 'Embarked', 'Sex'])['Age'].transform('mean'))
x_test['Age'] = x_test['Age'].fillna(x_train.groupby(['Pclass', 'Embarked', 'Sex'])['Age'].transform('mean'))

###
x_train['Fare'] = x_train['Fare'].fillna(x_train['Fare'].mean())
x_test['Fare'] = x_test['Fare'].fillna(x_train['Fare'].mean())

In [10]:
### Split train data in categorical and numerical data

def split_num_cat(dat):
        
    dat_num = dat.loc[:,(x_train.dtypes == 'float64')]
    dat_cat = dat.loc[:,~(x_train.dtypes == 'float64')]
    for i, col in enumerate(dat_cat.dtypes):
        if col == 'int64': 
            dat_cat.iloc[:,i] = dat_cat.iloc[:,i].astype('object') 
            
    return dat_num, dat_cat        

with warnings.catch_warnings():   
    warnings.simplefilter("ignore")
    x_train_num, x_train_cat = split_num_cat(x_train) 
    #x_val_num, x_val_cat = split_num_cat(x_val) 
    x_test_num, x_test_cat = split_num_cat(x_test) 

In [11]:
### Standardize numerical Data
scaler = StandardScaler()

x_train_num = scaler.fit_transform(x_train_num)
x_test_num = scaler.fit_transform(x_test_num)


In [12]:
### Impute and OneHotEncode categorical Data
impute_cat = SimpleImputer(strategy='most_frequent')
x_train_cat = impute_cat.fit_transform(x_train_cat)
#x_val_cat = impute_cat.fit_transform(x_val_cat)
x_test_cat = impute_cat.transform(x_test_cat)

onehot = OneHotEncoder(handle_unknown='ignore')
x_train_cat = onehot.fit_transform(x_train_cat)
x_train_cat = x_train_cat.toarray()
#x_val_cat = onehot.transform(x_val_cat)
#x_val_cat = x_val_cat.toarray()
x_test_cat = onehot.transform(x_test_cat)
x_test_cat = x_test_cat.toarray()

In [13]:
### Combine numerical and categorical datasets
x_train = np.hstack((x_train_num, x_train_cat))
#x_val = np.hstack((x_val_num, x_val_cat))
x_test = np.hstack((x_test_num, x_test_cat))

**Use halving GridSearch on a wide range of hyperparameters and then use exhaustive GridSearch on a narrower set of parameters**

In [14]:
from scikeras.wrappers import KerasClassifier

def build_model(units, lr, activation, drop_rate):
    
    optimizer = keras.optimizers.SGD(learning_rate=lr)
    deep_model = Sequential()
    deep_model.add(Input(shape=(18,)))
    
    hidden_layers = 4
    for deep_layer in range(hidden_layers): 
        deep_model.add(Dense(units=units/(deep_layer+1), kernel_initializer='HeNormal'))
        deep_model.add(Activation(activation))
        if deep_layer in (0,1):
            deep_model.add(Dropout(drop_rate))
        
    deep_model.add(Dense(units=1, activation='sigmoid', kernel_initializer='GlorotNormal'))

    deep_model.summary()
    deep_model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
    
    return deep_model


In [15]:
early_stopping = keras.callbacks.EarlyStopping(patience=20)
optimizer = keras.optimizers.SGD(learning_rate=4e-4)

deep_model = Sequential()
deep_model.add(Input(shape=(18,)))
deep_model.add(Dense(units=500, kernel_initializer='HeNormal'))
deep_model.add(Activation('relu'))
deep_model.add(Dropout(0.5))
deep_model.add(Dense(units=250, kernel_initializer='HeNormal'))
deep_model.add(Activation('relu'))
deep_model.add(Dropout(0.25))
deep_model.add(Dense(units=125, kernel_initializer='HeNormal'))
deep_model.add(Activation('relu'))
deep_model.add(Dense(units=30, kernel_initializer='HeNormal'))
deep_model.add(Activation('relu'))
deep_model.add(Dense(units=1, activation='sigmoid', kernel_initializer='GlorotNormal'))

deep_model.summary()
deep_model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
#deep_model.fit(x_train, y_train, validation_split=0.2, epochs=300, batch_size=32, callbacks=[early_stopping])

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 500)               9500      
                                                                 
 activation (Activation)     (None, 500)               0         
                                                                 
 dropout (Dropout)           (None, 500)               0         
                                                                 
 dense_1 (Dense)             (None, 250)               125250    
                                                                 
 activation_1 (Activation)   (None, 250)               0         
                                                                 
 dropout_1 (Dropout)         (None, 250)               0         
                                                                 
 dense_2 (Dense)             (None, 125)               3

In [16]:
### Do GridSearch for Random Forest, Support Vector Machine and Logistic Regression with Lasso Regularization
from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV, GridSearchCV 

early_stopping = keras.callbacks.EarlyStopping(patience=10)
model_check = keras.callbacks.ModelCheckpoint(filepath='best_model.h5', monitor='val_loss')


rfc = RandomForestClassifier()
llr = LogisticRegression(penalty='l1', solver='liblinear')
svc = SVC()
#gbc = GradientBoostingClassifier()
ada = AdaBoostClassifier(base_estimator=DecisionTreeClassifier())
xgbc = xgb.XGBClassifier()
models = [rfc, llr, svc, ada, xgbc]

param_grid_deep = {'activation': ['relu', 'selu'],
                   'drop_rate': [0.5, 0.3, 0],
                   'units': [500, 400, 300],
                   'lr': [3e-4, 2e-3, 1e-2]}

param_grid_rfc = {'n_estimators': [10, 50, 100, 200, 400],
                 'max_depth': [4, None],
                 'min_samples_split': [2, 4, 8],
                 'max_features': [2, 'log2', 0.5]}


param_grid_svc = {'C': [0.25, 0.5, 1.0, 2.0, 5.0, 10.0],
                 'kernel': ['linear', 'rbf', 'poly'],
                 'gamma': ['scale', 'auto']}


param_grid_llr = {'C': [0.25, 0.5, 1.0, 2.0, 5.0, 10.0]}

param_grid_ada = {'learning_rate': [1e-4, 1e-3, 1e-2, 1e-1],
                 'n_estimators': [30, 50, 100, 200, 400, 800]}

param_grid_xgbc = {'learning_rate': [1e-4, 1e-3, 1e-2, 1e-1],
                  'n_estimators': [30, 50, 100, 200, 400],
                  'max_depth': [2, 4, 8]}


param_grids = {'deep_model': (None, param_grid_deep),
               'rfc': (rfc, param_grid_rfc),
             # 'svc': (svc, param_grid_svc),
              'llr': (llr, param_grid_llr),
              'ada': (ada, param_grid_ada),
              'xgbc': (xgbc, param_grid_xgbc)}

cv_results = {}
for model in param_grids:
    if model == 'deep_model':
        print(f'GridSearch for {model}')
        deep_model = KerasClassifier(model=build_model, **param_grids[model][1], validation_split=0.2, callbacks=[early_stopping])
        models.insert(0, deep_model)
        deep_model_grid = GridSearchCV(deep_model, param_grids[model][1], cv=5, verbose=3)
        deep_model_grid.fit(x_train, y_train, epochs=200)
        cv_results[model] = (deep_model_grid.best_params_, round(deep_model_grid.best_score_, 3))
    else:
        print(f'GridSearch for {model}')
        search = GridSearchCV(param_grids[model][0], param_grids[model][1], verbose=1)
        search.fit(x_train, y_train)
        cv_results[model] = (search.best_params_, round(np.mean(search.cv_results_['mean_test_score']), 3))


GridSearch for deep_model
Fitting 5 folds for each of 54 candidates, totalling 270 fits
Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_5 (Dense)             (None, 500)               9500      
                                                                 
 activation_4 (Activation)   (None, 500)               0         
                                                                 
 dropout_2 (Dropout)         (None, 500)               0         
                                                                 
 dense_6 (Dense)             (None, 250)               125250    
                                                                 
 activation_5 (Activation)   (None, 250)               0         
                                                                 
 dropout_3 (Dropout)         (None, 250)               0         
                                

Epoch 45/200
18/18 [==============================] - 0s 9ms/step - loss: 0.6753 - accuracy: 0.6239 - val_loss: 0.5707 - val_accuracy: 0.7133
Epoch 46/200
18/18 [==============================] - 0s 7ms/step - loss: 0.6816 - accuracy: 0.5975 - val_loss: 0.5691 - val_accuracy: 0.7133
Epoch 47/200
18/18 [==============================] - 0s 10ms/step - loss: 0.6927 - accuracy: 0.6046 - val_loss: 0.5680 - val_accuracy: 0.7273
Epoch 48/200
18/18 [==============================] - 0s 10ms/step - loss: 0.6829 - accuracy: 0.6134 - val_loss: 0.5665 - val_accuracy: 0.7273
Epoch 49/200
18/18 [==============================] - 0s 8ms/step - loss: 0.6844 - accuracy: 0.6239 - val_loss: 0.5652 - val_accuracy: 0.7203
Epoch 50/200
18/18 [==============================] - 0s 9ms/step - loss: 0.6794 - accuracy: 0.6186 - val_loss: 0.5635 - val_accuracy: 0.7343
Epoch 51/200
18/18 [==============================] - 0s 8ms/step - loss: 0.6506 - accuracy: 0.6415 - val_loss: 0.5623 - val_accuracy: 0.7413
Epoc

18/18 [==============================] - 0s 9ms/step - loss: 0.5760 - accuracy: 0.6872 - val_loss: 0.4545 - val_accuracy: 0.8252
Epoch 160/200
18/18 [==============================] - 0s 6ms/step - loss: 0.5896 - accuracy: 0.7100 - val_loss: 0.4537 - val_accuracy: 0.8252
Epoch 161/200
18/18 [==============================] - 0s 8ms/step - loss: 0.5780 - accuracy: 0.7206 - val_loss: 0.4529 - val_accuracy: 0.8252
Epoch 162/200
18/18 [==============================] - 0s 7ms/step - loss: 0.5815 - accuracy: 0.6977 - val_loss: 0.4524 - val_accuracy: 0.8252
Epoch 163/200
18/18 [==============================] - 0s 7ms/step - loss: 0.5828 - accuracy: 0.7065 - val_loss: 0.4518 - val_accuracy: 0.8252
Epoch 164/200
18/18 [==============================] - 0s 7ms/step - loss: 0.5588 - accuracy: 0.7522 - val_loss: 0.4511 - val_accuracy: 0.8252
Epoch 165/200
18/18 [==============================] - 0s 8ms/step - loss: 0.5596 - accuracy: 0.7118 - val_loss: 0.4504 - val_accuracy: 0.8252
Epoch 166/200

Epoch 60/200
18/18 [==============================] - 0s 9ms/step - loss: 0.6339 - accuracy: 0.6368 - val_loss: 0.5593 - val_accuracy: 0.7483
Epoch 61/200
18/18 [==============================] - 0s 8ms/step - loss: 0.6509 - accuracy: 0.6474 - val_loss: 0.5578 - val_accuracy: 0.7483
Epoch 62/200
18/18 [==============================] - 0s 7ms/step - loss: 0.6037 - accuracy: 0.6842 - val_loss: 0.5563 - val_accuracy: 0.7483
Epoch 63/200
18/18 [==============================] - 0s 9ms/step - loss: 0.6440 - accuracy: 0.6175 - val_loss: 0.5548 - val_accuracy: 0.7483
Epoch 64/200
18/18 [==============================] - 0s 9ms/step - loss: 0.6756 - accuracy: 0.6070 - val_loss: 0.5535 - val_accuracy: 0.7483
Epoch 65/200
18/18 [==============================] - 0s 6ms/step - loss: 0.6442 - accuracy: 0.6754 - val_loss: 0.5519 - val_accuracy: 0.7552
Epoch 66/200
18/18 [==============================] - 0s 9ms/step - loss: 0.6433 - accuracy: 0.6368 - val_loss: 0.5505 - val_accuracy: 0.7552
Epoch 

18/18 [==============================] - 0s 10ms/step - loss: 0.5477 - accuracy: 0.7368 - val_loss: 0.4603 - val_accuracy: 0.8252
Epoch 175/200
18/18 [==============================] - 0s 9ms/step - loss: 0.5698 - accuracy: 0.7070 - val_loss: 0.4599 - val_accuracy: 0.8252
Epoch 176/200
18/18 [==============================] - 0s 9ms/step - loss: 0.5572 - accuracy: 0.7281 - val_loss: 0.4594 - val_accuracy: 0.8252
Epoch 177/200
18/18 [==============================] - 0s 9ms/step - loss: 0.5651 - accuracy: 0.6982 - val_loss: 0.4589 - val_accuracy: 0.8252
Epoch 178/200
18/18 [==============================] - 0s 9ms/step - loss: 0.5886 - accuracy: 0.7281 - val_loss: 0.4586 - val_accuracy: 0.8252
Epoch 179/200
18/18 [==============================] - 0s 8ms/step - loss: 0.5567 - accuracy: 0.7246 - val_loss: 0.4582 - val_accuracy: 0.8252
Epoch 180/200
18/18 [==============================] - 0s 9ms/step - loss: 0.5418 - accuracy: 0.7421 - val_loss: 0.4578 - val_accuracy: 0.8252
Epoch 181/20

...

                                                                 
 activation_1051 (Activation  (None, 100)              0         
 )                                                               
                                                                 
 dense_1314 (Dense)          (None, 1)                 101       
                                                                 
Total params: 128,034
Trainable params: 128,034
Non-trainable params: 0
_________________________________________________________________
Epoch 1/200
18/18 [==============================] - 1s 17ms/step - loss: 0.5592 - accuracy: 0.7667 - val_loss: 0.3876 - val_accuracy: 0.8322
Epoch 2/200
18/18 [==============================] - 0s 8ms/step - loss: 0.4312 - accuracy: 0.8035 - val_loss: 0.4007 - val_accuracy: 0.8182
Epoch 3/200
18/18 [==============================] - 0s 7ms/step - loss: 0.4223 - accuracy: 0.8175 - val_loss: 0.4051 - val_accuracy: 0.7902
Epoch 4/200
18/18 [=======================

                                                                 
 dense_1322 (Dense)          (None, 133)               26733     
                                                                 
 activation_1058 (Activation  (None, 133)              0         
 )                                                               
                                                                 
 dense_1323 (Dense)          (None, 100)               13400     
                                                                 
 activation_1059 (Activation  (None, 100)              0         
 )                                                               
                                                                 
 dense_1324 (Dense)          (None, 1)                 101       
                                                                 
Total params: 128,034
Trainable params: 128,034
Non-trainable params: 0
_________________________________________________________________
Epoc

 dense_1330 (Dense)          (None, 300)               5700      
                                                                 
 activation_1064 (Activation  (None, 300)              0         
 )                                                               
                                                                 
 dropout_532 (Dropout)       (None, 300)               0         
                                                                 
 dense_1331 (Dense)          (None, 150)               45150     
                                                                 
 activation_1065 (Activation  (None, 150)              0         
 )                                                               
                                                                 
 dropout_533 (Dropout)       (None, 150)               0         
                                                                 
 dense_1332 (Dense)          (None, 100)               15100     
          

Total params: 73,601
Trainable params: 73,601
Non-trainable params: 0
_________________________________________________________________
Epoch 1/200
18/18 [==============================] - 1s 15ms/step - loss: 0.5339 - accuracy: 0.7772 - val_loss: 0.3783 - val_accuracy: 0.8392
Epoch 2/200
18/18 [==============================] - 0s 8ms/step - loss: 0.4458 - accuracy: 0.8140 - val_loss: 0.3793 - val_accuracy: 0.8671
Epoch 3/200
18/18 [==============================] - 0s 8ms/step - loss: 0.4364 - accuracy: 0.8158 - val_loss: 0.3337 - val_accuracy: 0.8811
Epoch 4/200
18/18 [==============================] - 0s 8ms/step - loss: 0.4109 - accuracy: 0.8351 - val_loss: 0.3849 - val_accuracy: 0.8322
Epoch 5/200
18/18 [==============================] - 0s 7ms/step - loss: 0.4149 - accuracy: 0.8228 - val_loss: 0.3346 - val_accuracy: 0.8811
Epoch 6/200
18/18 [==============================] - 0s 6ms/step - loss: 0.4097 - accuracy: 0.8404 - val_loss: 0.3310 - val_accuracy: 0.8881
Epoch 7/200
18/18

 activation_1085 (Activation  (None, 250)              0         
 )                                                               
                                                                 
 dropout_543 (Dropout)       (None, 250)               0         
                                                                 
 dense_1357 (Dense)          (None, 166)               41666     
                                                                 
 activation_1086 (Activation  (None, 166)              0         
 )                                                               
                                                                 
 dense_1358 (Dense)          (None, 125)               20875     
                                                                 
 activation_1087 (Activation  (None, 125)              0         
 )                                                               
                                                                 
 dense_135

In [17]:
cv_results

{'deep_model': ({'activation': 'selu',
   'drop_rate': 0,
   'lr': 0.002,
   'units': 500},
  0.828),
 'rfc': ({'max_depth': None,
   'max_features': 0.5,
   'min_samples_split': 8,
   'n_estimators': 10},
  0.821),
 'llr': ({'C': 5.0}, 0.825),
 'ada': ({'learning_rate': 0.1, 'n_estimators': 800}, 0.787),
 'xgbc': ({'learning_rate': 0.1, 'max_depth': 2, 'n_estimators': 400}, 0.816)}

In [18]:
### Get best cross-validated Model and fit it on whole training dataset
max_acc = 0
best_model = 0
for model_idx, model in enumerate(cv_results):
    if cv_results[model][1] > max_acc:
        max_acc = cv_results[model][1]
        best_model = model_idx

    
best = models[best_model].set_params(**cv_results[list(cv_results.keys())[best_model]][0])   
if best_model == 0:
    best.fit(x_train, y_train, validation_split=0.2, epochs=400, callbacks=[early_stopping])
else:    
    best.fit(x_train, y_train)
y_predict = best.predict(x_test)        
predictions = pd.DataFrame({'PassengerId': test_passenger_ids, 'Survived': y_predict})

print(best_model)
# Save predictions to csv file
predictions.to_csv('Titanic_Submission.csv', index=False)

Model: "sequential_272"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_1360 (Dense)          (None, 500)               9500      
                                                                 
 activation_1088 (Activation  (None, 500)              0         
 )                                                               
                                                                 
 dropout_544 (Dropout)       (None, 500)               0         
                                                                 
 dense_1361 (Dense)          (None, 250)               125250    
                                                                 
 activation_1089 (Activation  (None, 250)              0         
 )                                                               
                                                                 
 dropout_545 (Dropout)       (None, 250)            